## BigDL-Nano Keras Inference Example
---
This example shows the usage of BigDL-Nano Tensorflow Keras inference pipeline.

In [1]:
import os
from time import time

import numpy as np
import tensorflow as tf
import tensorflow_datasets as tfds
from tensorflow import keras
from tensorflow.keras import layers
from bigdl.nano.tf.keras import Model

In [2]:
IMG_SIZE=224
BATCH_SIZE=64
DATASET_NAME="stanford_dogs"

### Loading data
---
Here we load data from tensorflow_datasets (hereafter TFDS). Stanford Dogs dataset is provided in TFDS as stanford_dogs. It features 20,580 images that belong to 120 classes of dog breeds (12,000 for training and 8,580 for testing).

In [3]:
(_, ds_test), ds_info=tfds.load(
    DATASET_NAME, data_dir="tensorflow_datasets/" ,split=["train", "train"], with_info=True, as_supervised=True
)
NUM_CLASSES = ds_info.features["label"].num_classes

size = (IMG_SIZE, IMG_SIZE)
ds_test = ds_test.map(lambda image, label: (tf.image.resize(image, size), label))

2022-06-07 08:30:34.765214: I tensorflow/core/platform/cpu_feature_guard.cc:151] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [4]:
def input_preprocess(image, label):
    label = tf.one_hot(label, NUM_CLASSES)
    return image, label

ds_test = ds_test.map(input_preprocess)
TEST_STEPS = int(os.environ.get('TEST_STEPS', len(ds_test)))
ds_test = ds_test.take(TEST_STEPS)

### Loading Model
---
Load the EfficientNetB0 Model using the H5 file saving using bigdl.nano.tf.keras.Model after single process training in the nano-keras-fit-example.

In [5]:
model = keras.models.load_model("EfficientNetB0.h5")

In [6]:
start = time()
model.predict(ds_test.batch(64))
inference_time_model_basic = time() - start

tcmalloc: large alloc 1073741824 bytes == 0x55b28622c000 @  0x7f7e60cc8d3f 0x7f7e60cff0c0 0x7f7e60d02082 0x7f7e60d02243 0x7f7e43092402 0x7f7e3742ceb0 0x7f7e3744d0b5 0x7f7e374509ea 0x7f7e37450f69 0x7f7e374512d1 0x7f7e37445ce3 0x7f7e32b0b051 0x7f7e3296638d 0x7f7e326f9087 0x7f7e326f991e 0x7f7e326f9b1d 0x7f7e3e0eabf5 0x7f7e32b0cd7c 0x7f7e32a96cec 0x7f7e37e5976e 0x7f7e37e561f3 0x7f7e331e8313 0x7f7e60c5e609 0x7f7e60b83133


### Quantize Model
---
Use Model.quantize from bigdl.nano.tf.keras to calibrate a keras model for post-training quantization.<br>
Here are the parameters used in the notebook:
```
    :param calib_dataset:  A tf.data.Dataset object for calibration. Required for
                            static quantization.
    :param val_dataset:    A tf.data.Dataset object for evaluation.
    :param batch:          Batch size of dataloader for both calib_dataset and val_dataset.
    :param metric:         A Metric object for evaluation.
    
    :param tuning_strategy:    'bayesian', 'basic', 'mse', 'sigopt'. Default: 'bayesian'.
    
```
Access more details from [Source](https://github.com/intel-analytics/BigDL/blob/main/python/nano/src/bigdl/nano/tf/quantization.py#L22)

In [7]:
model_quantized = model.quantize(calib_dataset=ds_test.batch(64),
                                 metric=tf.keras.metrics.CategoricalAccuracy(),
                                 tuning_strategy='bayesian'
                                 )

2022-06-07 04:23:07 [WARNING] Override the value of `metric` field defined in yaml file as user defines the value of `metric` attribute by code.
2022-06-07 04:23:07.861366: I tensorflow/core/grappler/devices.cc:75] Number of eligible GPUs (core count >= 8, compute capability >= 0.0): 0 (Note: TensorFlow was not compiled with CUDA or ROCm support)
2022-06-07 04:23:07.861591: I tensorflow/core/grappler/clusters/single_machine.cc:358] Starting new session
2022-06-07 04:23:07.902605: I tensorflow/core/grappler/optimizers/meta_optimizer.cc:1149] Optimization results for grappler item: graph_to_optimize
  function_optimizer: function_optimizer did nothing. time = 0.016ms.
  function_optimizer: function_optimizer did nothing. time = 0.003ms.

2022-06-07 04:23:09.256227: I tensorflow/core/grappler/devices.cc:75] Number of eligible GPUs (core count >= 8, compute capability >= 0.0): 0 (Note: TensorFlow was not compiled with CUDA or ROCm support)
2022-06-07 04:23:09.256405: I tensorflow/core/grap

Instructions for updating:
Use `tf.compat.v1.graph_util.extract_sub_graph`


2022-06-07 04:23:11 [WARNING] From /opt/conda/envs/nanoWithTf/lib/python3.7/site-packages/neural_compressor/adaptor/tf_utils/util.py:322: extract_sub_graph (from tensorflow.python.framework.graph_util_impl) is deprecated and will be removed in a future version.
Instructions for updating:
Use `tf.compat.v1.graph_util.extract_sub_graph`
2022-06-07 04:23:11 [INFO] Pass StripUnusedNodesOptimizer elapsed time: 464.52 ms
2022-06-07 04:23:11 [INFO] Pass GraphCseOptimizer elapsed time: 120.49 ms
2022-06-07 04:23:12 [INFO] Pass FoldBatchNormNodesOptimizer elapsed time: 783.94 ms
2022-06-07 04:23:12 [INFO] Pass UpdateEnterOptimizer elapsed time: 28.49 ms
2022-06-07 04:23:12 [INFO] Pass ConvertLeakyReluOptimizer elapsed time: 32.47 ms
2022-06-07 04:23:12 [INFO] Pass ConvertAddToBiasAddOptimizer elapsed time: 32.76 ms
2022-06-07 04:23:12 [INFO] Pass FuseTransposeReshapeOptimizer elapsed time: 33.09 ms
2022-06-07 04:23:12 [INFO] Pass FuseConvWithMathOptimizer elapsed time: 32.58 ms
2022-06-07 04:23

Instructions for updating:
This function will only be available through the v1 compatibility library as tf.compat.v1.saved_model.utils.build_tensor_info or tf.compat.v1.saved_model.build_tensor_info.


2022-06-07 04:24:14 [WARNING] From /opt/conda/envs/nanoWithTf/lib/python3.7/site-packages/tensorflow/python/saved_model/signature_def_utils_impl.py:208: build_tensor_info (from tensorflow.python.saved_model.utils_impl) is deprecated and will be removed in a future version.
Instructions for updating:
This function will only be available through the v1 compatibility library as tf.compat.v1.saved_model.utils.build_tensor_info or tf.compat.v1.saved_model.build_tensor_info.


...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

 -2.25904512 -2.52339649 -0.329480648 -0.921312094 -3.20745683 -1.53407359 -2.88393164 -0.920381546 -1.76087582 -3.53810358 -3.23206306 -1.36140394 1.12078786 -2.33845758 0.883744955 -1.38437438 -1.18397939 -4.29397964 3.3362329 -1.31663752 -1.9810611 -0.620040655 -4.59684896 0.694036245 1.07939231 -1.72338772 1.79178536 -2.36944103 -1.76575375 0.563286901 -3.49270582 0.23149848 -2.75253177 -0.678557217 -3.64825 -2.01377606 -2.36523294 -0.675490379 -1.65436399 -1.21261716 -3.16678715 2.01708484 0.33205843 -0.308283687 -2.98061395 -1.52169156 -4.54607964 -2.56634665 2.93084192 -4.22359085 -2.34777355 -0.914489508 -4.46421623 -1.26459062 -0.6282444 0.152509212 -1.42

2022-06-07 04:29:29 [INFO] Start sampling on calibration dataset.
;EfficientNet/stem_conv/Conv2D_eightbit_min_EfficientNet/stem_conv_pad/Pad__print__;__min:[0]
;EfficientNet/stem_conv/Conv2D_eightbit_max_EfficientNet/stem_conv_pad/Pad__print__;__max:[1]
;EfficientNet/stem_conv/Conv2D_eightbit_requant_range__print__;__requant_min:[-16.6541328]
;EfficientNet/stem_conv/Conv2D_eightbit_requant_range__print__;__requant_max:[21.5224571]
;EfficientNet/block1a_se_reduce/Conv2D_eightbit_min_EfficientNet/block1a_se_reshape/Reshape__print__;__min:[-0.275394917]
;EfficientNet/block1a_se_reduce/Conv2D_eightbit_max_EfficientNet/block1a_se_reshape/Reshape__print__;__max:[15.0205612]
;EfficientNet/block1a_se_reduce/Conv2D_eightbit_requant_range__print__;__requant_min:[-4.10535812]
;EfficientNet/block1a_se_reduce/Conv2D_eightbit_requant_range__print__;__requant_max:[-1.48294878]
;EfficientNet/block1a_se_expand/Conv2D_eightbit_min_EfficientNet/block1a_se_reduce/mul__print__;__min:[-0.27431944]
;Efficien

;EfficientNet/block5c_project_conv/Conv2D_eightbit_min_EfficientNet/block5c_se_excite/mul__print__;__min:[-0.255543441]
;EfficientNet/block5c_project_conv/Conv2D_eightbit_max_EfficientNet/block5c_se_excite/mul__print__;__max:[12.9150925]
;EfficientNet/block5c_project_conv/Conv2D_eightbit_requant_range__print__;__requant_min:[-19.5194569]
;EfficientNet/block5c_project_conv/Conv2D_eightbit_requant_range__print__;__requant_max:[20.3025894]
;EfficientNet/block6a_expand_conv/Conv2D_eightbit_min_EfficientNet/block5c_add/add__print__;__min:[-38.8998795]
;EfficientNet/block6a_expand_conv/Conv2D_eightbit_max_EfficientNet/block5c_add/add__print__;__max:[39.5121269]
;EfficientNet/block6a_expand_conv/Conv2D_eightbit_requant_range__print__;__requant_min:[-11.5431557]
;EfficientNet/block6a_expand_conv/Conv2D_eightbit_requant_range__print__;__requant_max:[13.6583843]
;EfficientNet/block6a_se_reduce/Conv2D_eightbit_min_EfficientNet/block6a_se_reshape/Reshape__print__;__min:[-0.271459937]
;EfficientNet

;EfficientNet/block2b_se_reduce/Conv2D_eightbit_min_EfficientNet/block2b_se_reshape/Reshape__print__;__min:[-0.278456897]
;EfficientNet/block2b_se_reduce/Conv2D_eightbit_max_EfficientNet/block2b_se_reshape/Reshape__print__;__max:[3.63701963]
;EfficientNet/block2b_se_reduce/Conv2D_eightbit_requant_range__print__;__requant_min:[-0.0524663553]
;EfficientNet/block2b_se_reduce/Conv2D_eightbit_requant_range__print__;__requant_max:[6.17646885]
;EfficientNet/block2b_se_expand/Conv2D_eightbit_min_EfficientNet/block2b_se_reduce/mul__print__;__min:[-0.0255451556]
;EfficientNet/block2b_se_expand/Conv2D_eightbit_max_EfficientNet/block2b_se_reduce/mul__print__;__max:[6.16366243]
;EfficientNet/block2b_se_expand/Conv2D_eightbit_requant_range__print__;__requant_min:[-5.11612701]
;EfficientNet/block2b_se_expand/Conv2D_eightbit_requant_range__print__;__requant_max:[5.82428598]
;EfficientNet/block2b_project_conv/Conv2D_eightbit_min_EfficientNet/block2b_se_excite/mul__print__;__min:[-0.276271164]
;Efficien

2022-06-07 04:29:31 [INFO] Pass QuantizedRNNConverter elapsed time: 19.57 ms
2022-06-07 04:29:32 [INFO] Pass StripUnusedNodesOptimizer elapsed time: 41.59 ms
2022-06-07 04:29:32 [INFO] Pass RemoveTrainingNodesOptimizer elapsed time: 15.77 ms
2022-06-07 04:29:32 [INFO] Pass FoldBatchNormNodesOptimizer elapsed time: 13.76 ms
2022-06-07 04:29:32 [INFO] Pass MetaOpOptimizer elapsed time: 8.11 ms
2022-06-07 04:29:32 [INFO] Pass PostCseOptimizer elapsed time: 129.13 ms
2022-06-07 04:29:32 [INFO] |**********Mixed Precision Statistics*********|
2022-06-07 04:29:32 [INFO] +-----------------------+-------+------+------+
2022-06-07 04:29:32 [INFO] |        Op Type        | Total | INT8 | FP32 |
2022-06-07 04:29:32 [INFO] +-----------------------+-------+------+------+
2022-06-07 04:29:32 [INFO] |         Conv2D        |   65  |  65  |  0   |
2022-06-07 04:29:32 [INFO] | DepthwiseConv2dNative |   16  |  0   |  16  |
2022-06-07 04:29:32 [INFO] |         MatMul        |   1   |  1   |  0   |
2022-06

In [8]:
images = np.random.random((len(ds_test), 224, 224, 3))

tcmalloc: large alloc 14489223168 bytes == 0x55b4817ae000 @  0x7f7e60cc8d3f 0x7f7e60cff0c0 0x7f7e60cff61a 0x7f7e55fd1ead 0x7f7e55fd1f27 0x7f7e56014794 0x7f7e5601531f 0x7f7e560aac25 0x7f7e55b420bc 0x7f7e55bf4fc8 0x55b236473db5 0x7f7e55bf4c71 0x55b2364b0fc4 0x55b2364b10e1 0x55b23650d1cc 0x55b23644e059 0x55b23644ef24 0x55b23644ef4c 0x55b236517f7d 0x55b2364b0e49 0x55b2364b10e1 0x55b23650cb14 0x55b2364aa092 0x55b236509dda 0x55b2364aa092 0x55b236509dda 0x55b2364aa092 0x55b2364b0dec 0x55b2364b114f 0x55b23650cfa9 0x55b2364b007b


In [9]:
start = time()
with model_quantized.sess as sess:
    sess.run(model_quantized.output_tensor,
             feed_dict={model_quantized.input_tensor[0]: images})
infer_time_model_quantized = time() - start

tcmalloc: large alloc 7244611584 bytes == 0x55b7e19ae000 @  0x7f7e60cc8d3f 0x7f7e60cff0c0 0x7f7e60cff61a 0x7f7e55fd1ead 0x7f7e55fd1f27 0x7f7e56014794 0x7f7e56014aca 0x7f7e56014cd3 0x7f7e56017f10 0x7f7e5601812f 0x7f7e560affa7 0x55b2364b0f7c 0x55b2364b10e1 0x55b23650d782 0x55b2364b007b 0x55b2365088b0 0x55b23644e059 0x55b2364b0307 0x55b236509841 0x55b23644e059 0x55b23644ef24 0x55b23644ef4c 0x55b236517f7d 0x55b2364b0e49 0x55b2364b10e1 0x55b23650cb14 0x55b2364aa092 0x55b236509dda 0x55b2364aa092 0x55b236509dda 0x55b2364aa092
tcmalloc: large alloc 8589934592 bytes == 0x55b991eae000 @  0x7f7e60cc8d3f 0x7f7e60cff0c0 0x7f7e60d02082 0x7f7e60d02243 0x7f7e43092402 0x7f7e3742ceb0 0x7f7e3744ca93 0x7f7e374509ea 0x7f7e37450f69 0x7f7e374512d1 0x7f7e37445ce3 0x7f7e32b0b051 0x7f7e3296638d 0x7f7e326f9087 0x7f7e326f991e 0x7f7e326f9b1d 0x7f7e399d2bf7 0x7f7e3b8f83ee 0x7f7e32b0cd7c 0x7f7e32a96cec 0x7f7e37e5976e 0x7f7e37e561f3 0x7f7e331e8313 0x7f7e60c5e609 0x7f7e60b83133
tcmalloc: large alloc 8589934592 bytes =

In [10]:
template = """
|    Precision   | Inference Time(s) |
|      FP32      |       {:5.2f}       |
|      INT8      |       {:5.2f}       |
| Improvement(%) |       {:5.2f}       |
"""
summary = template.format(
    inference_time_model_basic,
    infer_time_model_quantized,
    (1 - infer_time_model_quantized /inference_time_model_basic) * 100
)
print(summary)


|    Precision   | Inference Time(s) |
|      FP32      |       43.63       |
|      INT8      |       38.53       |
| Improvement(%) |       11.69       |

